In [2007]:
import pandas as pd
import numpy as np
import string
import re
import nltk

In [2008]:
df = pd.read_csv('DataScientist.csv',index_col=0) #index_col specifies the index column so the unnamed column doesnt appear
df = df.drop("Job Description", axis=1)
df.head(10)





index                          Job Title               Salary Estimate  \
0      0              Senior Data Scientist  $111K-$181K (Glassdoor est.)   
1      1  Data Scientist, Product Analytics  $111K-$181K (Glassdoor est.)   
2      2               Data Science Manager  $111K-$181K (Glassdoor est.)   
3      3                       Data Analyst  $111K-$181K (Glassdoor est.)   
4      4             Director, Data Science  $111K-$181K (Glassdoor est.)   
5      5                     Data Scientist  $111K-$181K (Glassdoor est.)   
6      6            Quantitative Researcher  $111K-$181K (Glassdoor est.)   
7      7    Quantitative Research Associate  $111K-$181K (Glassdoor est.)   
8      8                       AI Scientist  $111K-$181K (Glassdoor est.)   
9      9            Quantitative Researcher  $111K-$181K (Glassdoor est.)   

   Rating                     Company Name       Location      Headquarters  \
0     3.5                      Hopper\n3.5   New York, NY  Montreal, Canada   
1     4.5                     Noom US\n4.5   New York, NY      New York, NY   
2    -1.0                         Decode_M   New York, NY      New York, NY   
3     3.4            Sapphire Digital\n3.4  Lyndhurst, NJ     Lyndhurst, NJ   
4     3.4  United Entertainment Group\n3.4   New York, NY      New York, NY   
5     2.9               IFG Companies\n2.9   New York, NY      Hartford, CT   
6     4.4                PDT Partners\n4.4   New York, NY      New York, NY   
7    -1.0           Enlightenment Research   New York, NY      New York, NY   
8     5.0                       Paige\n5.0   New York, NY      New York, NY   
9     4.8                 Jane Street\n4.8   New York, NY      New York, NY   

                     Size  Founded  Type of ownership  \
0   501 to 1000 employees     2007  Company - Private   
1  1001 to 5000 employees     2008  Company - Private   
2       1 to 50 employees       -1            Unknown   
3    201 to 500 employees     2019  Company - Private   
4     51 to 200 employees     2007  Company - Private   
5    201 to 500 employees     1985  Company - Private   
6     51 to 200 employees     1993  Company - Private   
7       1 to 50 employees       -1            Unknown   
8       1 to 50 employees     2018  Company - Private   
9   501 to 1000 employees     2000  Company - Private   

                                  Industry                  Sector  \
0                          Travel Agencies        Travel & Tourism   
1                Health, Beauty, & Fitness       Consumer Services   
2                                       -1                      -1   
3                                 Internet  Information Technology   
4                  Advertising & Marketing       Business Services   
5                       Insurance Carriers               Insurance   
6    Investment Banking & Asset Management                 Finance   
7                                       -1                      -1   
8  Enterprise Software & Network Solutions  Information Technology   
9    Investment Banking & Asset Management                 Finance   

                    Revenue                    Competitors Easy Apply  
0  Unknown / Non-Applicable                             -1         -1  
1  Unknown / Non-Applicable                             -1         -1  
2  Unknown / Non-Applicable                             -1       True  
3  Unknown / Non-Applicable           Zocdoc, Healthgrades         -1  
4  Unknown / Non-Applicable       BBDO, Grey Group, Droga5         -1  
5  Unknown / Non-Applicable  Colony Specialty, Markel, RLI         -1  
6  Unknown / Non-Applicable                             -1         -1  
7  Unknown / Non-Applicable                             -1       True  
8  Unknown / Non-Applicable                             -1       True  
9  Unknown / Non-Applicable                             -1         -1

In [2009]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 3909 entries, 0 to 3908
Data columns (total 15 columns):
 #   Column             Non-Null Count  Dtype  
---  ------             --------------  -----  
 0   index              3909 non-null   int64  
 1   Job Title          3909 non-null   object 
 2   Salary Estimate    3909 non-null   object 
 3   Rating             3909 non-null   float64
 4   Company Name       3909 non-null   object 
 5   Location           3909 non-null   object 
 6   Headquarters       3909 non-null   object 
 7   Size               3909 non-null   object 
 8   Founded            3909 non-null   int64  
 9   Type of ownership  3909 non-null   object 
 10  Industry           3909 non-null   object 
 11  Sector             3909 non-null   object 
 12  Revenue            3909 non-null   object 
 13  Competitors        3909 non-null   object 
 14  Easy Apply         3909 non-null   object 
dtypes: float64(1), int64(2), object(12)
memory usage: 488.6+ KB


In [2010]:
def convert_String_to_Bool(entry):
    """Converting column to bool values in column "Easy Apply"

    Args:
        entry (str): column consisted of strings 

    Returns:
        bool : bool type column
    """
    
    if entry == "-1":
        return False
    return True

df["Easy Apply"] = df["Easy Apply"].apply(lambda x : convert_String_to_Bool(x))
df["Easy Apply"].value_counts()

False    3745
True      164
Name: Easy Apply, dtype: int64

In [2011]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 3909 entries, 0 to 3908
Data columns (total 15 columns):
 #   Column             Non-Null Count  Dtype  
---  ------             --------------  -----  
 0   index              3909 non-null   int64  
 1   Job Title          3909 non-null   object 
 2   Salary Estimate    3909 non-null   object 
 3   Rating             3909 non-null   float64
 4   Company Name       3909 non-null   object 
 5   Location           3909 non-null   object 
 6   Headquarters       3909 non-null   object 
 7   Size               3909 non-null   object 
 8   Founded            3909 non-null   int64  
 9   Type of ownership  3909 non-null   object 
 10  Industry           3909 non-null   object 
 11  Sector             3909 non-null   object 
 12  Revenue            3909 non-null   object 
 13  Competitors        3909 non-null   object 
 14  Easy Apply         3909 non-null   bool   
dtypes: bool(1), float64(1), int64(2), object(11)
memory usage: 461.9+ KB


In [2012]:

df.replace((['-1',"-1.0",-1]), [np.nan,np.nan,np.nan], inplace=True) # by looking at the data set we can tell that -1 is a replacment for a None value so were changing all -1 to NaN

In [2013]:
df.head()

index                          Job Title               Salary Estimate  \
0      0              Senior Data Scientist  $111K-$181K (Glassdoor est.)   
1      1  Data Scientist, Product Analytics  $111K-$181K (Glassdoor est.)   
2      2               Data Science Manager  $111K-$181K (Glassdoor est.)   
3      3                       Data Analyst  $111K-$181K (Glassdoor est.)   
4      4             Director, Data Science  $111K-$181K (Glassdoor est.)   

   Rating                     Company Name       Location      Headquarters  \
0     3.5                      Hopper\n3.5   New York, NY  Montreal, Canada   
1     4.5                     Noom US\n4.5   New York, NY      New York, NY   
2     NaN                         Decode_M   New York, NY      New York, NY   
3     3.4            Sapphire Digital\n3.4  Lyndhurst, NJ     Lyndhurst, NJ   
4     3.4  United Entertainment Group\n3.4   New York, NY      New York, NY   

                     Size  Founded  Type of ownership  \
0   501 to 1000 employees   2007.0  Company - Private   
1  1001 to 5000 employees   2008.0  Company - Private   
2       1 to 50 employees      NaN            Unknown   
3    201 to 500 employees   2019.0  Company - Private   
4     51 to 200 employees   2007.0  Company - Private   

                    Industry                  Sector  \
0            Travel Agencies        Travel & Tourism   
1  Health, Beauty, & Fitness       Consumer Services   
2                        NaN                     NaN   
3                   Internet  Information Technology   
4    Advertising & Marketing       Business Services   

                    Revenue               Competitors  Easy Apply  
0  Unknown / Non-Applicable                       NaN       False  
1  Unknown / Non-Applicable                       NaN       False  
2  Unknown / Non-Applicable                       NaN        True  
3  Unknown / Non-Applicable      Zocdoc, Healthgrades       False  
4  Unknown / Non-Applicable  BBDO, Grey Group, Droga5       False

In [2014]:
df.isnull().sum()

#df.info()

index                   0
Job Title               0
Salary Estimate         0
Rating                409
Company Name            0
Location                0
Headquarters          240
Size                  229
Founded               977
Type of ownership     229
Industry              546
Sector                546
Revenue               229
Competitors          2760
Easy Apply              0
dtype: int64

In [2015]:
def salary_parser_min(salary_string: str):
  """Creating a new column for minimum salary

  Args:
      salary_string (str): Salary Estitmate column which we are splitting into 2 new columns being minimum and maximum

  Returns:
      str : returns the first column after splitting the args column
  """
  salary_split = salary_string.split()
  salary = salary_split[0]
  del salary_split
  salary = salary.replace("K", "")
  salary = salary.replace("$", "")
  salary_range = salary.split("-")
  return salary_range[0]

df["Minimum Salary"] = df["Salary Estimate"].apply(lambda x : salary_parser_min(x))
#df["Minimum Salary"] = df["Minimum Salary"].astype(int)

df["Minimum Salary"].value_counts()




46     149
39     127
55     124
74     120
93     101
      ... 
59      12
17      11
66       9
10       3
146      3
Name: Minimum Salary, Length: 82, dtype: int64

In [2016]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 3909 entries, 0 to 3908
Data columns (total 16 columns):
 #   Column             Non-Null Count  Dtype  
---  ------             --------------  -----  
 0   index              3909 non-null   int64  
 1   Job Title          3909 non-null   object 
 2   Salary Estimate    3909 non-null   object 
 3   Rating             3500 non-null   float64
 4   Company Name       3909 non-null   object 
 5   Location           3909 non-null   object 
 6   Headquarters       3669 non-null   object 
 7   Size               3680 non-null   object 
 8   Founded            2932 non-null   float64
 9   Type of ownership  3680 non-null   object 
 10  Industry           3363 non-null   object 
 11  Sector             3363 non-null   object 
 12  Revenue            3680 non-null   object 
 13  Competitors        1149 non-null   object 
 14  Easy Apply         3909 non-null   bool   
 15  Minimum Salary     3909 non-null   object 
dtypes: bool(1), float64(2), 

In [2017]:
def salary_parser_max(salary_string: str):
  """Creating a new column for minimum salary

  Args:
      salary_string (str): Salary Estitmate column which we are splitting into 2 new columns being minimum and maximum

  Returns:
      str : returns the second column after splitting the args column
  """
  salary_split = salary_string.split()
  salary = salary_split[0]
  del salary_split
  salary = salary.replace("K", "")
  salary = salary.replace("$", "")
  salary_range = salary.split("-")
  return salary_range[1]

df["Maximum Salary"] = df["Salary Estimate"].apply(lambda x : salary_parser_max(x))
#df["Maximum Salary"] = df["Maximum Salary"].astype(float)

df["Minimum Salary"].value_counts()



46     149
39     127
55     124
74     120
93     101
      ... 
59      12
17      11
66       9
10       3
146      3
Name: Minimum Salary, Length: 82, dtype: int64

In [2018]:
df["Maximum Salary"].info()

<class 'pandas.core.series.Series'>
Int64Index: 3909 entries, 0 to 3908
Series name: Maximum Salary
Non-Null Count  Dtype 
--------------  ----- 
3909 non-null   object
dtypes: object(1)
memory usage: 61.1+ KB


In [2019]:
df.drop('Salary Estimate',axis = 1,inplace = True)
df['Company Name'] = df['Company Name'].str.replace('\n.*', ' ',regex=True) #removing \n. from the column "company name"
#df['Est_Salary']= (df['Minimum Salary']+df['Maximum Salary'])/2

In [2020]:
df["Location"].head(10)

0     New York, NY
1     New York, NY
2     New York, NY
3    Lyndhurst, NJ
4     New York, NY
5     New York, NY
6     New York, NY
7     New York, NY
8     New York, NY
9     New York, NY
Name: Location, dtype: object

In [2021]:

def spliting_location_and_HQ (entry : object, geo_type : str) -> str:
    """Splits the location and HQ column to a city column and a state column.

    Args:
        entry (object,str): Location column we want to split. 2nd argument is either "city" or "state"

    Returns:
        str: returns either a locaton_city, locaton_state, HQ_city or HQ_state column
    """
    entry = str(entry)
    
    if entry == "nan":
        return None
    entry = entry.replace(" ", "")
    location_HQ_split = entry.split(",")
    location_HQ_city_state = location_HQ_split
    if geo_type == "city":
        return location_HQ_city_state[0]
    else:
        return location_HQ_city_state[1]


df["Location_City"]=df["Location"].apply(lambda x: spliting_location_and_HQ(x,"city"))
df["Location_State"]=df["Location"].apply(lambda x: spliting_location_and_HQ(x,"state"))
df["HQ_City"]=df["Headquarters"].apply(lambda x: spliting_location_and_HQ(x,"city"))
df["HQ_State"]=df["Headquarters"].apply(lambda x: spliting_location_and_HQ(x,"state"))

df.head()

    

      index                                                                                                                                          Job Title  Rating                                           Company Name                            Location                         Headquarters                     Size  Founded               Type of ownership                                  Industry                              Sector                           Revenue                                                                                   Competitors  Easy Apply Minimum Salary Maximum Salary                Location_City Location_State                   HQ_City       HQ_State
0         0                                                                                                                              Senior Data Scientist     3.5                                                Hopper                         New York, NY                     Montreal, Canada    501 to 1

In [2022]:
def splitting_department_from_job_title (entry : str, key_word : str) -> str:
    """Splitting Department from Job title in the column "Job Title"
    
    Args:
        entry (str, str): parse the column as an str, 2nd argument is either job_title or department.
    Returns:
        str: returns a new column at the end of the dataset
    """
    
    department_job_title = entry.split(",")
    job_title = department_job_title[0]
    department = department_job_title[-1]
    if key_word == "Job Title":
        return job_title
    else:
        
        return department

df["Department"] = df["Job Title"].apply(lambda x: splitting_department_from_job_title(x,"department"))    
df["Job Title"] = df["Job Title"].apply(lambda x: splitting_department_from_job_title(x,"Job Title"))
df["Job_title"] = df["Job Title"]
df.drop("Job Title",axis=1, inplace=True)


    
    

In [2023]:
df.head()

      index  Rating                                           Company Name                            Location                         Headquarters                     Size  Founded               Type of ownership                                  Industry                              Sector                           Revenue                                                                                   Competitors  Easy Apply Minimum Salary Maximum Salary                Location_City Location_State                   HQ_City       HQ_State                                                                                                              Department                                                                                                               Job_title
0         0     3.5                                                Hopper                         New York, NY                     Montreal, Canada    501 to 1000 employees   2007.0               Company - Private

In [2024]:
df["Job_title"].value_counts()

Data Scientist                                       335
Data Engineer                                        268
Data Analyst                                         264
Senior Data Scientist                                104
Senior Data Analyst                                   52
                                                    ... 
Principal Device Modeling Engineer                     1
SQL/SAS Data Analyst                                   1
Marketing Data Analyst Coordinator                     1
Greenplum /Big Data Engineer/Architect                 1
Patient Safety Physician or Safety Scientist - UK      1
Name: Job_title, Length: 1797, dtype: int64

In [2025]:
df["Job_title"] = df["Job_title"].str.replace(" â","")
df["Job_title"] = df["Job_title"].str.replace("/","|")



In [2026]:
df["Revenue"].value_counts()

Unknown / Non-Applicable            1163
$10+ billion (USD)                   599
$100 to $500 million (USD)           338
$50 to $100 million (USD)            214
$2 to $5 billion (USD)               211
$10 to $25 million (USD)             191
$1 to $2 billion (USD)               180
$1 to $5 million (USD)               170
$25 to $50 million (USD)             143
$5 to $10 billion (USD)              133
Less than $1 million (USD)           124
$500 million to $1 billion (USD)     114
$5 to $10 million (USD)              100
Name: Revenue, dtype: int64

In [2027]:

df["Revenue"] = df["Revenue"].replace("Unknown / Non-Applicable",np.nan)
df['Revenue'] = df['Revenue'].str.replace('$', ' ',regex=True)
df['Revenue'] = df['Revenue'].str.replace('(USD)', ' ',regex=True)
df['Revenue'] = df['Revenue'].str.replace('(', ' ',regex=True)
df['Revenue'] = df['Revenue'].str.replace(')', ' ',regex=True)
df['Revenue'] = df['Revenue'].str.replace(' ', '',regex=True)
df['Revenue'] = df['Revenue'].str.replace('+', '',regex=True)
df['Revenue'] = df['Revenue'].str.replace('2to5billion', '2billionto5billion')
df['Revenue'] = df['Revenue'].str.replace('5to10billion ', '5billionto10billion')
df['Revenue'] = df['Revenue'].replace('million', ' ')
df['Revenue'] = df['Revenue'].replace('10billion', '10billionto11billion')
df['Revenue'] = df['Revenue'].str.replace('Lessthan1million', '0millionto1million')
df['Revenue'] = df['Revenue'].str.replace('million', ' ')
df['Revenue'] = df['Revenue'].str.replace('billion', '000 ')
df["Revenue"] = df["Revenue"].str.replace(" to","to")

In [2028]:
df["Revenue"].value_counts()

10000to11000     599
100to500         338
50to100          214
2000to5000       211
10to25           191
1to2000          180
1to5             170
25to50           143
5to10000         133
0to1             124
500to1000        114
5to10            100
Name: Revenue, dtype: int64

In [2029]:
def splitting_revenue(entry: object, key_word: str) -> str:
    """splits the revenue to a max and a min revenue column

    Args:
        entry (object), key_word (str): Revenue column 

    Returns:
        str: returns either a minimum or maximum column dependent on key_word
    """
    entry = str(entry)
    
    if entry == "nan":
        return None
    min_max = entry.split("to")
    if key_word == "min":
        return min_max[0]
    else:
        return min_max[-1]
    
df["min_revenue_in_milions"]=df["Revenue"].apply(lambda x: splitting_revenue(x,"min"))
df["max_revenue_in_milions"]=df["Revenue"].apply(lambda x: splitting_revenue(x,"max"))
df.drop("Revenue",axis=1,inplace=True)
    

In [2030]:
df["min_revenue_in_milions"].value_counts()

10000    599
1        350
100      338
5        233
50       214
2000     211
10       191
25       143
0        124
500      114
Name: min_revenue_in_milions, dtype: int64

In [2031]:

df.head(10)

index  Rating                 Company Name       Location  \
0      0     3.5                      Hopper    New York, NY   
1      1     4.5                     Noom US    New York, NY   
2      2     NaN                     Decode_M   New York, NY   
3      3     3.4            Sapphire Digital   Lyndhurst, NJ   
4      4     3.4  United Entertainment Group    New York, NY   
5      5     2.9               IFG Companies    New York, NY   
6      6     4.4                PDT Partners    New York, NY   
7      7     NaN       Enlightenment Research   New York, NY   
8      8     5.0                       Paige    New York, NY   
9      9     4.8                 Jane Street    New York, NY   

       Headquarters                    Size  Founded  Type of ownership  \
0  Montreal, Canada   501 to 1000 employees   2007.0  Company - Private   
1      New York, NY  1001 to 5000 employees   2008.0  Company - Private   
2      New York, NY       1 to 50 employees      NaN            Unknown   
3     Lyndhurst, NJ    201 to 500 employees   2019.0  Company - Private   
4      New York, NY     51 to 200 employees   2007.0  Company - Private   
5      Hartford, CT    201 to 500 employees   1985.0  Company - Private   
6      New York, NY     51 to 200 employees   1993.0  Company - Private   
7      New York, NY       1 to 50 employees      NaN            Unknown   
8      New York, NY       1 to 50 employees   2018.0  Company - Private   
9      New York, NY   501 to 1000 employees   2000.0  Company - Private   

                                  Industry                  Sector  ...  \
0                          Travel Agencies        Travel & Tourism  ...   
1                Health, Beauty, & Fitness       Consumer Services  ...   
2                                      NaN                     NaN  ...   
3                                 Internet  Information Technology  ...   
4                  Advertising & Marketing       Business Services  ...   
5                       Insurance Carriers               Insurance  ...   
6    Investment Banking & Asset Management                 Finance  ...   
7                                      NaN                     NaN  ...   
8  Enterprise Software & Network Solutions  Information Technology  ...   
9    Investment Banking & Asset Management                 Finance  ...   

  Minimum Salary  Maximum Salary Location_City Location_State    HQ_City  \
0            111             181       NewYork             NY   Montreal   
1            111             181       NewYork             NY    NewYork   
2            111             181       NewYork             NY    NewYork   
3            111             181     Lyndhurst             NJ  Lyndhurst   
4            111             181       NewYork             NY    NewYork   
5            111             181       NewYork             NY   Hartford   
6            111             181       NewYork             NY    NewYork   
7            111             181       NewYork             NY    NewYork   
8            111             181       NewYork             NY    NewYork   
9            111             181       NewYork             NY    NewYork   

  HQ_State                       Department                        Job_title  \
0   Canada            Senior Data Scientist            Senior Data Scientist   
1       NY                Product Analytics                   Data Scientist   
2       NY             Data Science Manager             Data Science Manager   
3       NJ                     Data Analyst                     Data Analyst   
4       NY                     Data Science                         Director   
5       CT                   Data Scientist                   Data Scientist   
6       NY          Quantitative Researcher          Quantitative Researcher   
7       NY  Quantitative Research Associate  Quantitative Research Associate   
8       NY                     AI Scientist                     AI Scientist   
9       N

In [2044]:
df["min_revenue_in_milions"].value_counts()

10000    599
1        350
100      338
5        233
50       214
2000     211
10       191
25       143
0        124
500      114
Name: min_revenue_in_milions, dtype: int64

In [2032]:
df["HQ_State"] = df["HQ_State"].str.replace("Sweden","SWE")
df["HQ_State"] = df["HQ_State"].str.replace("Belgium","BE")
df["HQ_State"] = df["HQ_State"].str.replace("Iran","IR")
df["HQ_State"] = df["HQ_State"].str.replace("United Kingdom","UK")

In [2033]:
df["Founded"] = df["Founded"].astype("Int32") #rounding to a 32 bit so the year in the column looks nicer


In [2034]:
df["Company Name"] = df["Company Name"].astype(str)


In [2035]:
for i in df.index: #fixing the index column to align the  default index
    df.loc[i,"index"] = i
        

In [2036]:
df["Type of ownership"] = df["Type of ownership"].str.replace("/","|")

In [2037]:
df["Size"].value_counts()

10000+ employees           993
51 to 200 employees        563
1001 to 5000 employees     553
1 to 50 employees          550
201 to 500 employees       418
501 to 1000 employees      307
5001 to 10000 employees    219
Unknown                     77
Name: Size, dtype: int64

In [2038]:
df["Size"] = df["Size"].str.replace("employees","",regex=True)
df["Size"] = df["Size"].str.replace("+","to10001",regex=True)
df["Size"] = df["Size"].str.replace(" ","",regex=True)
df["Size"] = df["Size"].replace("Unknown",np.nan)


In [2047]:
df["min_size_emp"]=df["Size"].apply(lambda x: splitting_revenue(x,"min")) #using splitting_revenue method to split size aswell since they have the same deno.
df["max_size_emp"]=df["Size"].apply(lambda x: splitting_revenue(x,"max")) 
df.drop("Size",axis=1,inplace=True)



0     501
1    1001
2       1
3     201
4      51
Name: min_size_emp, dtype: object

In [2043]:
df.head()